In [8]:
import json
import requests
from auo_tests.tasks.config import host

In [9]:
dag_script = {
    "sub_nodes": [
        {
            "id": "1",
            "name": "SqlNode1",
            "op": "sql",
            "script": "select * from train",
        },
        {
            "id": "2",
            "name": "SqlNode1",
            "op": "sql",
            "script": "select * from test",
        },
        {
            "id": "3",
            "name": "PysparkNode1",
            "op": "pyspark",  # or python
            "inputs": {'train': ("1", 0),
                       'test': ("2", 0)
                       },
            "script": "",
        },
    ],
    "edges": [
        ("1", "2"),
        ("2", "3")
    ]
}
with open('./spark_script_1012.py', 'r') as f:
    pyspark_script = f.read()
dag_script["sub_nodes"][2]["script"] = pyspark_script


##### 创建sparks作业

In [10]:
data = {
    "name": "sparks_test_group1012",
    "file_urls": [],
    "script": json.dumps(dag_script),
    "cmd": "",
    "cmd_parameters": "",
    "envs": {},
    "run_image": "SXKJ:32775/jupyter:dag",
    "task_type": "sparks",
    "user_id": 33
}
print(f'http://{host}/jpt/af_task')
ret = requests.post(url=f'http://{host}/jpt/af_task', json=data)
print(ret.json())

http://192.168.199.109:18082/jpt/af_task
{'code': 200, 'data': {'name': 'sparks_test_group1012', 'file_urls': [], 'cmd': '', 'envs': {}, 'create_time': 1665561957, 'user_id': 33, 'task_type': 'sparks', 'id': 49, 'script': '{"sub_nodes": [{"id": "1", "name": "SqlNode1", "op": "sql", "script": "select * from train"}, {"id": "2", "name": "SqlNode1", "op": "sql", "script": "select * from test"}, {"id": "3", "name": "PysparkNode1", "op": "pyspark", "inputs": {"train": ["1", 0], "test": ["2", 0]}, "script": "from pyspark.sql.types import *\\nfrom pyspark.ml.classification import LogisticRegression\\nfrom pyspark.ml.feature import VectorAssembler\\nfrom pyspark.ml import Pipeline\\nfrom pyspark.sql.functions import udf, col\\nfrom pyspark.sql import DataFrame\\n\\n\\ndef to_array(col):\\n    def to_array_(v):\\n        return v.toArray().tolist()\\n\\n    return udf(to_array_, ArrayType(DoubleType())).asNondeterministic()(col)\\n\\n\\ndef main_func(train_df: DataFrame, test_df: DataFrame, spa

##### 用task创建/更新job

In [13]:
ret = requests.get(url=f'http://{host}/jpt/af_task/getOnce/49')

In [17]:
task_info = ret.json()['data']

In [21]:
data_item = {
    "tasks": [
        task_info
    ],
    "name": "test_sparks_job",
    "dependence": [],
    "cron": "0 0 * * 0",
    "desc": "string",
    "route_strategy": "string",
    "block_strategy": "string",
    "executor_timeout": 0,
    "executor_fail_retry_count": 0,
    "trigger_status": 0,
    "job_mode": 2,
}

In [22]:
is_update = False
if is_update:
    ret = requests.post(url=f'http://{host}/jpt/af_job',json=data_item)
    print(ret.json())
else:
    ret = requests.put(url=f'http://{host}/jpt/af_job/35',json=data_item)
    ret = requests.post(url=f'http://{host}/jpt/af_job/submit?id=35')
    print(ret.json())

{'code': 200, 'data': None, 'msg': ''}


In [ ]:
ret = requests.post(url=f'http://{host}/jpt/af_job/submit',json=new_item)
print(ret.json())

In [1]:
from datetime import timedelta
delta1 = timedelta(seconds=57)
delta2 = timedelta(hours=25, seconds=2)
delta2 != delta1

delta2 == 5

False